![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo J 2013 Utilização de Serviços de Saúde

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [ ]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

## Definição do peso e filtragem de respondentes do questionário

In [ ]:
#Selecionando registros válidos e calculando peso amostral 
pns2013.1<-<Coloque aqui o nome do arquivo RDATA> %>% filter(V0015==1) 
pns2013.1<-pns2013.1 %>% mutate(peso_moradores=((V00281*205546/199551444)))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_moradores))
summary(pns2013.1$peso_moradores)

## Criação de variáveis dos indicadores

In [ ]:
#Desfechos - Indicadores

#Consulta médica nos últimos 12 meses - J001P
pns2013.1 <- pns2013.1 %>% mutate(J001P= ifelse(J011==1, 1,0))
pns2013.1$J001P<-factor(pns2013.1$J001P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2013.1$J001P)

#Consulta odontológica nos últimos 12 meses - J002P
pns2013.1 <- pns2013.1 %>% mutate(J002P= ifelse(J013==1, 1,0))
pns2013.1$J002P<-factor(pns2013.1$J002P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2013.1$J002P)

#Procura por atendimento de saúde nas últimas duas semanas - J003P
pns2013.1 <- pns2013.1 %>% mutate(J003P= ifelse(J014==1, 1,0))
pns2013.1$J003P<-factor(pns2013.1$J003P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2013.1$J003P)

#Fonte usual de cuidados - J004P
pns2013.1 <- pns2013.1 %>% mutate(J004P= ifelse(J009==1, 1,0))
pns2013.1$J004P<-factor(pns2013.1$J004P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2013.1$J004P)

#Internação hospitalar por 24h ou mais nos últimos 12 meses - J005P
pns2013.1 <- pns2013.1 %>% mutate(J005P= ifelse(J037==1, 1,0))
pns2013.1$J005P<-factor(pns2013.1$J005P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2013.1$J005P)

# Utilização de alguma prática integrativa e complementar nos últimos 12 meses - J011P
pns2013.1 <- pns2013.1 %>% mutate(J011P= ifelse(J053==1, 1,0))
pns2013.1$J011P<-factor(pns2013.1$J011P, levels=c(1,0), labels=c("Sim", "Não"))
summary(pns2013.1$J011P)

## Definições de abrangências

### Situação urbana ou rural

In [ ]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Situação_Urbano_Rural=V0026)
pns2013.1$Situação_Urbano_Rural<-factor(pns2013.1$Situação_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2013.1$Situação_Urbano_Rural)

### Sexo

In [ ]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

### UF

In [ ]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federação=V0001)
pns2013.1$Unidades_da_Federação<-factor(pns2013.1$Unidades_da_Federação, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federação)

### Grandes Regiões

In [ ]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federação, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

### Capital

In [ ]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federação,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$Capital)

### Faixa Etária

In [ ]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(-Inf,0.99, 4.99, 14.99, 24.99,34.99,44.99,59.99,Inf),
  labels = c("Menor de 1 ano","1 a 4 anos","5 a 14 anos","15 a 24 anos","25 a 34 anos","35 a 44 anos","45 a 59 anos","60 anos ou mais"), 
  ordered_result = TRUE, right = TRUE))
summary(pns2013.1$faixa_idade) 

### Raça

In [ ]:
#Raça
pns2013.1 <- pns2013.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2 , 2, 
                        ifelse(C009==4, 3,
                        ifelse(C009==9, 9, 4)))))
pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3,4),labels=c("Branca", "Preta", "Parda", "Outras"))
summary(pns2013.1$Raca)

### Renda per capita

In [ ]:
#Rendimento domiciliar per capita 
pns2013.1 <-  pns2013.1 %>% drop_na(VDF003) %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034,Inf),
  labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM","2 até 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))

summary(pns2013.1$rend_per_capita)


## Criando indicadores

### Filtrando base de indicadores

In [ ]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2013survey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_moradores", "J001P","J002P","J003P", "J004P","J005P","J011P","V0031","C008",
                                     "Situação_Urbano_Rural","Sexo","Unidades_da_Federação", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita")
summary(pns2013survey)

### Exporta tabela filtrada com os dados específicos - Módulo J 2013

In [ ]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2013survey, file.path(diretorio_saida, "pns2013Isurvey.csv"))

### Cria plano amostral complexo

In [ ]:
#survey design
desPNS=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_moradores,nest=TRUE, data=pns2013survey)
desPNS_C=subset(desPNS, V0031==1)
desPNS_R=subset(desPNS, !is.na(Raca))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [ ]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [ ]:
ListaIndicadores = c(~J001P,~J002P,~J003P,~J004P,~J005P,~J011P)
ListaIndicadoresTexto = c("J001P","J002P","J003P","J004P","J005P","J011P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Situação_Urbano_Rural,~Unidades_da_Federação,~GrandesRegioes,~Capital)
ListaDominiosTexto = c("Sexo","raça","rend_per_capita","faixa_idade","urb_rur","uf","região","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

#### Preenchendo a tabela de indicadores

In [ ]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
               if (ListaDominiosTexto[j]=="capital"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNS_C , svymean,vartype= c("ci","cv"))
               }else if (ListaDominiosTexto[j]=="raça"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNS_R , svymean,vartype= c("ci","cv"))
               }else {
                   dataframe_indicador<-svyby( indicador , dominio , desPNS , svymean,vartype= c("ci","cv"))
               }
               
                dataframe_indicador<-data.frame(dataframe_indicador)
              
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}

#### Criando a tabela pela abrangência total

In [ ]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [ ]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        dataframe_indicador_N <- data.frame()
         if (total == "Capital"){
                dataframe_indicador <- svymean(indicador,desPNS_C)
        } else {
                   dataframe_indicador <- svymean(indicador,desPNS)
        }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano
        
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
    }
}

#### Unindo tabela de indicadores e de totais

In [ ]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [ ]:
matrizIndicadores

#### Exportando tabela de indicadores calculados - Módulo J 2013

In [ ]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores, file=paste0(diretorio_saida, "Indicadores_2013J_R.csv"), sep = ";",dec = ",", row.names = FALSE)